In [37]:

# Análisis Exploratorio de Datos - Modelo de Fuga Colsubsidio
# ================================================================
# 
# Objetivo: Análisis completo de los datos para entender patrones de fuga
# - Distribución de la variable target y desbalance de clases
# - Calidad y completitud de los datos
# - Patrones en variables financieras y demográficas
# - Impacto de beneficios Colsubsidio en retención
# - Insights para feature engineering y modelado

# =============================================================================
# CONFIGURACIÓN INICIAL
# =============================================================================
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.figure_factory as ff
import warnings
import sys
from pathlib import Path

# Configuración de visualización
plt.style.use('default')
sns.set_palette("husl")
warnings.filterwarnings('ignore')

# Configurar plotly para notebooks
import plotly.offline as pyo
pyo.init_notebook_mode(connected=True)

print("Librerías cargadas exitosamente")
print(f"Análisis iniciado: {pd.Timestamp.now()}")



Librerías cargadas exitosamente
Análisis iniciado: 2025-08-15 07:32:39.299053


In [38]:
# =============================================================================
# CARGA DE DATOS
# =============================================================================
import sys
import pandas as pd
from pathlib import Path

# Ruta base de los datos
data_path = Path("../data/raw")

# Cargar datasets principales
train = pd.read_excel(data_path / "train.xlsx")
test = pd.read_excel(data_path / "test.xlsx")

# Inicializar diccionario para guardar todos los datasets cargados
datasets = {
    "train": train,
    "test": test
}

#  Cargar datos complementarios
try:
    demograficas = pd.read_excel(data_path / "train_test_demograficas.xlsx")
    subsidios = pd.read_excel(data_path / "train_test_subsidios.xlsx")
    
    datasets["demograficas"] = demograficas
    datasets["subsidios"] = subsidios
    
    # Integrar datos en train y test
    train_integrated = train.merge(demograficas, on="id", how="left") \
                                       .merge(subsidios, on="id", how="left")
    test_integrated = test.merge(demograficas, on="id", how="left") \
                                     .merge(subsidios, on="id", how="left")
    
    datasets["train_integrated"] = train_integrated
    datasets["test_integrated"] = test_integrated
    
except FileNotFoundError:
    print("⚠️ Archivos complementarios no encontrados. Usando solo datos principales.")

# Imprimir información de todos los datasets cargados
print("\n=== DATASETS CARGADOS ===")
for name, df in datasets.items():
    if isinstance(df, pd.DataFrame):
        print(f"{name.upper()}: {len(df):,} registros x {len(df.columns)} columnas")





=== DATASETS CARGADOS ===
TRAIN: 50,001 registros x 22 columnas
TEST: 5,001 registros x 20 columnas
DEMOGRAFICAS: 55,002 registros x 10 columnas
SUBSIDIOS: 55,002 registros x 4 columnas
TRAIN_INTEGRATED: 50,001 registros x 34 columnas
TEST_INTEGRATED: 5,001 registros x 32 columnas


In [39]:
# =============================================================================
# ESTRUCTURA Y DISTRIBUCIÓN TARGET
# =============================================================================

print("=" * 60)
print("ANÁLISIS FUGA COLSUBSIDIO - DATASET TRAIN")
print("=" * 60)

train = datasets["train"]

# Información básica
print(f"Total clientes: {train.shape[0]:,}")
print(f"Variables disponibles: {train.shape[1]}")

# Distribución del problema de fuga
target_counts = train['Target'].value_counts()
churn_rate = (target_counts[1] / target_counts.sum()) * 100

print(f"\nDistribución fuga:")
print(f"  Clientes activos: {target_counts[0]:,} ({100-churn_rate:.1f}%)")
print(f"  Clientes fuga: {target_counts[1]:,} ({churn_rate:.1f}%)")
print(f"  Desbalance: {target_counts[0]/target_counts[1]:.1f}:1")

# Contexto de negocio
if churn_rate < 5:
   print(f"  Escenario: Fuga controlada - optimización preventiva")
else:
   print(f"  Escenario: Fuga alta - intervención urgente")

# Análisis de completitud por tipo de variable
print(f"\nCompletitud variables:")

# Variables administrativas (solo Target=1 por diseño)
vars_admin = ['Cancelacion', 'Gestionable', 'ANO_MES', 'TIPO']
admin_missing = train[vars_admin].isnull().sum()
print(f"  Variables administrativas (Target=1 únicamente):")
for var in vars_admin:
   pct_missing = (admin_missing[var] / len(train)) * 100
   print(f"    {var}: {100-pct_missing:.1f}% completo")

# Variables financieras (todos los clientes)
vars_financieras = ['Saldo', 'Limite.Cupo', 'Edad.Mora', 'Pago.del.Mes']
fin_missing = train[vars_financieras].isnull().sum()
print(f"  Variables financieras:")
for var in vars_financieras:
   pct_missing = (fin_missing[var] / len(train)) * 100
   print(f"    {var}: {100-pct_missing:.1f}% completo")

# Fechas de referencia
print(f"\nReferencias temporales:")
if 'Fecha.Proceso' in train.columns:
   fechas_proceso = train['Fecha.Proceso'].nunique()
   print(f"  Fechas análisis: {fechas_proceso} única(s)")
   
if 'Fecha.Expedicion' in train.columns:
   expediciones_validas = train['Fecha.Expedicion'].notna().sum()
   print(f"  Cupos con fecha expedición: {expediciones_validas:,}")

ANÁLISIS FUGA COLSUBSIDIO - DATASET TRAIN
Total clientes: 50,001
Variables disponibles: 22

Distribución fuga:
  Clientes activos: 48,589 (97.2%)
  Clientes fuga: 1,412 (2.8%)
  Desbalance: 34.4:1
  Escenario: Fuga controlada - optimización preventiva

Completitud variables:
  Variables administrativas (Target=1 únicamente):
    Cancelacion: 2.8% completo
    Gestionable: 2.8% completo
    ANO_MES: 2.8% completo
    TIPO: 2.8% completo
  Variables financieras:
    Saldo: 100.0% completo
    Limite.Cupo: 100.0% completo
    Edad.Mora: 100.0% completo
    Pago.del.Mes: 100.0% completo

Referencias temporales:
  Fechas análisis: 16 única(s)
  Cupos con fecha expedición: 50,001


In [40]:
# =============================================================================
# LIMPIEZA VARIABLES FINANCIERAS
# =============================================================================

def limpiar_financiera(serie, nombre):
   """Convierte formato '1 050 000.00' a float"""
   serie_clean = serie.astype(str).str.replace(' ', '').str.replace(',', '')
   serie_clean = serie_clean.replace('nan', np.nan)
   return pd.to_numeric(serie_clean, errors='coerce')

print(f"\nLimpieza variables financieras:")

train_clean = train.copy()

# Variables que requieren limpieza de formato
vars_monetarias = [
   'Saldo', 'Limite.Cupo', 'Disponible.Avances', 'Limite.Avances',
   'Total.Intereses', 'Saldos.Mes.Ant', 'Pagos.Mes.Ant', 'Vtas.Mes.Ant',
   'Pago.del.Mes', 'Pago.Minimo', 'Vr.Mora', 'Vr.Cuota.Manejo'
]

for var in vars_monetarias:
   if var in train_clean.columns:
       antes = train_clean[var].dtype
       train_clean[var] = limpiar_financiera(train_clean[var], var)
       despues = train_clean[var].dtype
       valores_validos = train_clean[var].notna().sum()
       print(f"  {var}: {antes} → {despues} ({valores_validos:,} válidos)")

# Verificar limpieza exitosa
vars_texto_restantes = train_clean.select_dtypes(include=['object']).columns
vars_financieras_texto = [v for v in vars_texto_restantes if v in vars_monetarias]

if not vars_financieras_texto:
   print(f"  ✓ Limpieza completada - todas las variables financieras son numéricas")
else:
   print(f"  ⚠ Variables pendientes: {vars_financieras_texto}")

# Estadísticas básicas post-limpieza
print(f"\nEstadísticas principales:")
vars_principales = ['Saldo', 'Limite.Cupo', 'Edad.Mora', 'Vr.Mora']

for var in vars_principales:
   if var in train_clean.columns:
       stats = train_clean[var].describe()
       ceros = (train_clean[var] == 0).sum()
       print(f"  {var}:")
       print(f"    Rango: ${stats['min']:,.0f} - ${stats['max']:,.0f}")
       print(f"    Promedio: ${stats['mean']:,.0f}")
       print(f"    Ceros: {ceros:,} ({ceros/len(train_clean)*100:.1f}%)")

datasets["train_clean"] = train_clean


Limpieza variables financieras:
  Saldo: object → float64 (50,001 válidos)
  Limite.Cupo: object → float64 (50,001 válidos)
  Disponible.Avances: object → float64 (50,001 válidos)
  Limite.Avances: object → float64 (50,001 válidos)
  Total.Intereses: object → float64 (50,001 válidos)
  Saldos.Mes.Ant: object → float64 (50,001 válidos)
  Pagos.Mes.Ant: object → float64 (50,001 válidos)
  Vtas.Mes.Ant: object → float64 (50,001 válidos)
  Pago.del.Mes: object → float64 (50,001 válidos)
  Pago.Minimo: object → float64 (50,001 válidos)
  Vr.Mora: object → float64 (50,001 válidos)
  Vr.Cuota.Manejo: object → float64 (50,001 válidos)
  ✓ Limpieza completada - todas las variables financieras son numéricas

Estadísticas principales:
  Saldo:
    Rango: $0 - $18,937,684
    Promedio: $340,878
    Ceros: 24,047 (48.1%)
  Limite.Cupo:
    Rango: $150,000 - $1,400,000,000
    Promedio: $1,265,604
    Ceros: 0 (0.0%)
  Edad.Mora:
    Rango: $0 - $4,050
    Promedio: $90
    Ceros: 41,316 (82.6%)
  

In [41]:
# =============================================================================
# ANÁLISIS DE RIESGO CREDITICIO
# =============================================================================

print(f"\nAnálisis riesgo crediticio:")

# 1. MORA - Variable crítica de riesgo
print(f"  Distribución días en mora:")
mora_stats = train_clean['Edad.Mora'].describe()
print(f"    Promedio: {mora_stats['mean']:.1f} días")
print(f"    Máximo: {mora_stats['max']:.0f} días")

# Clientes en mora vs sin mora
sin_mora = (train_clean['Edad.Mora'] == 0).sum()
con_mora = (train_clean['Edad.Mora'] > 0).sum()
print(f"    Sin mora: {sin_mora:,} ({sin_mora/len(train_clean)*100:.1f}%)")
print(f"    Con mora: {con_mora:,} ({con_mora/len(train_clean)*100:.1f}%)")

# Mora por target
if con_mora > 0:
   mora_fuga = train_clean[train_clean['Target']==1]['Edad.Mora'].mean()
   mora_no_fuga = train_clean[train_clean['Target']==0]['Edad.Mora'].mean()
   print(f"    Mora promedio - Fuga: {mora_fuga:.1f} días vs No fuga: {mora_no_fuga:.1f} días")

# 2. UTILIZACIÓN DE CUPO
train_clean['utilizacion_cupo'] = train_clean['Saldo'] / train_clean['Limite.Cupo']
train_clean['utilizacion_cupo'] = train_clean['utilizacion_cupo'].fillna(0).clip(0, 2)

print(f"\n  Utilización de cupo:")
util_stats = train_clean['utilizacion_cupo'].describe()
print(f"    Promedio: {util_stats['mean']:.2f}")
print(f"    Mediana: {util_stats['50%']:.2f}")

# Utilización por target
util_fuga = train_clean[train_clean['Target']==1]['utilizacion_cupo'].mean()
util_no_fuga = train_clean[train_clean['Target']==0]['utilizacion_cupo'].mean()
print(f"    Utilización - Fuga: {util_fuga:.2f} vs No fuga: {util_no_fuga:.2f}")

# 3. COMPORTAMIENTO DE PAGOS
train_clean['ratio_pago'] = train_clean['Pago.del.Mes'] / train_clean['Pago.Minimo']
train_clean['ratio_pago'] = train_clean['ratio_pago'].fillna(0).clip(0, 10)

sin_pago = (train_clean['Pago.del.Mes'] == 0).sum()
print(f"\n  Comportamiento pagos:")
print(f"    Sin pagos en el mes: {sin_pago:,} ({sin_pago/len(train_clean)*100:.1f}%)")

# Pagos por target
pago_fuga = train_clean[train_clean['Target']==1]['Pago.del.Mes'].mean()
pago_no_fuga = train_clean[train_clean['Target']==0]['Pago.del.Mes'].mean()
print(f"    Pago promedio - Fuga: ${pago_fuga:,.0f} vs No fuga: ${pago_no_fuga:,.0f}")

# 4. SEGMENTACIÓN POR ACTIVIDAD
# Clientes activos: tienen saldo > 0 o realizaron pagos
activos = ((train_clean['Saldo'] > 0) | (train_clean['Pago.del.Mes'] > 0)).sum()
inactivos = len(train_clean) - activos

print(f"\n  Segmentación actividad:")
print(f"    Clientes activos: {activos:,} ({activos/len(train_clean)*100:.1f}%)")
print(f"    Clientes inactivos: {inactivos:,} ({inactivos/len(train_clean)*100:.1f}%)")

# Fuga por actividad
if activos > 0:
   mask_activos = (train_clean['Saldo'] > 0) | (train_clean['Pago.del.Mes'] > 0)
   fuga_activos = train_clean[mask_activos]['Target'].mean() * 100
   fuga_inactivos = train_clean[~mask_activos]['Target'].mean() * 100
   print(f"    Tasa fuga activos: {fuga_activos:.1f}%")
   print(f"    Tasa fuga inactivos: {fuga_inactivos:.1f}%")


Análisis riesgo crediticio:
  Distribución días en mora:


    Promedio: 90.3 días
    Máximo: 4050 días
    Sin mora: 41,316 (82.6%)
    Con mora: 8,685 (17.4%)
    Mora promedio - Fuga: 2.1 días vs No fuga: 92.9 días

  Utilización de cupo:
    Promedio: 0.35
    Mediana: 0.00
    Utilización - Fuga: 0.11 vs No fuga: 0.36

  Comportamiento pagos:
    Sin pagos en el mes: 44,969 (89.9%)
    Pago promedio - Fuga: $32,347 vs No fuga: $12,688

  Segmentación actividad:
    Clientes activos: 26,022 (52.0%)
    Clientes inactivos: 23,979 (48.0%)
    Tasa fuga activos: 3.8%
    Tasa fuga inactivos: 1.8%


In [42]:
# =============================================================================
# ANTIGÜEDAD Y ACTIVIDAD CREDITICIA
# =============================================================================

print(f"\nAntigüedad y actividad crediticia:")

# 1. ANTIGÜEDAD DEL CUPO (Fecha.Expedicion)
if 'Fecha.Expedicion' in train_clean.columns:
   expedicion_valida = train_clean['Fecha.Expedicion'].notna().sum()
   print(f"  Cupos con fecha expedición: {expedicion_valida:,}")
   
   if expedicion_valida > 1000:  # Solo analizar si hay datos suficientes
       # Convertir fechas para calcular antigüedad
       train_clean['fecha_expedicion'] = pd.to_datetime(train_clean['Fecha.Expedicion'], errors='coerce')
       train_clean['fecha_proceso'] = pd.to_datetime(train_clean['Fecha.Proceso'], errors='coerce')
       
       # Calcular antigüedad en días
       train_clean['antiguedad_dias'] = (train_clean['fecha_proceso'] - train_clean['fecha_expedicion']).dt.days
       
       antiguedad_stats = train_clean['antiguedad_dias'].describe()
       print(f"    Antigüedad promedio: {antiguedad_stats['mean']:.0f} días ({antiguedad_stats['mean']/365:.1f} años)")
       print(f"    Rango: {antiguedad_stats['min']:.0f} - {antiguedad_stats['max']:.0f} días")
       
       # Antigüedad por target
       ant_fuga = train_clean[train_clean['Target']==1]['antiguedad_dias'].mean()
       ant_no_fuga = train_clean[train_clean['Target']==0]['antiguedad_dias'].mean()
       if pd.notna(ant_fuga) and pd.notna(ant_no_fuga):
           print(f"    Antigüedad - Fuga: {ant_fuga:.0f} días vs No fuga: {ant_no_fuga:.0f} días")

# 2. COMPARACIÓN MES ANTERIOR VS ACTUAL
print(f"\n  Evolución mes anterior:")

# Cambio en saldo
train_clean['cambio_saldo'] = train_clean['Saldo'] - train_clean['Saldos.Mes.Ant']
cambio_positivo = (train_clean['cambio_saldo'] > 0).sum()
cambio_negativo = (train_clean['cambio_saldo'] < 0).sum()
sin_cambio = (train_clean['cambio_saldo'] == 0).sum()

print(f"    Incremento saldo: {cambio_positivo:,} ({cambio_positivo/len(train_clean)*100:.1f}%)")
print(f"    Reducción saldo: {cambio_negativo:,} ({cambio_negativo/len(train_clean)*100:.1f}%)")
print(f"    Sin cambio: {sin_cambio:,} ({sin_cambio/len(train_clean)*100:.1f}%)")

# Cambio promedio por target
cambio_fuga = train_clean[train_clean['Target']==1]['cambio_saldo'].mean()
cambio_no_fuga = train_clean[train_clean['Target']==0]['cambio_saldo'].mean()
print(f"    Cambio promedio - Fuga: ${cambio_fuga:,.0f} vs No fuga: ${cambio_no_fuga:,.0f}")

# 3. PERFIL DE RIESGO COMBINADO
# Crear score de riesgo simple
conditions = [
   (train_clean['Edad.Mora'] > 30) & (train_clean['utilizacion_cupo'] > 0.8),
   (train_clean['Edad.Mora'] > 0) | (train_clean['utilizacion_cupo'] > 0.9),
   (train_clean['utilizacion_cupo'] > 0.7) | (train_clean['Vr.Mora'] > 0),
   True
]
choices = ['Alto', 'Medio_Alto', 'Medio', 'Bajo']
train_clean['perfil_riesgo'] = np.select(conditions, choices)

print(f"\n  Distribución perfil de riesgo:")
riesgo_dist = train_clean['perfil_riesgo'].value_counts()
for perfil, count in riesgo_dist.items():
   pct = count / len(train_clean) * 100
   print(f"    {perfil}: {count:,} ({pct:.1f}%)")

# Tasa de fuga por perfil de riesgo
print(f"  Tasa fuga por perfil:")
for perfil in ['Alto', 'Medio_Alto', 'Medio', 'Bajo']:
   if perfil in train_clean['perfil_riesgo'].values:
       tasa_fuga = train_clean[train_clean['perfil_riesgo']==perfil]['Target'].mean() * 100
       print(f"    {perfil}: {tasa_fuga:.1f}%")


Antigüedad y actividad crediticia:
  Cupos con fecha expedición: 50,001
    Antigüedad promedio: 1752 días (4.8 años)
    Rango: -333 - 4375 días
    Antigüedad - Fuga: 691 días vs No fuga: 1782 días

  Evolución mes anterior:
    Incremento saldo: 1,948 (3.9%)
    Reducción saldo: 4,527 (9.1%)
    Sin cambio: 43,526 (87.1%)
    Cambio promedio - Fuga: $-25,877 vs No fuga: $1

  Distribución perfil de riesgo:
    Bajo: 35,555 (71.1%)
    Medio_Alto: 8,532 (17.1%)
    Alto: 3,592 (7.2%)
    Medio: 2,322 (4.6%)
  Tasa fuga por perfil:
    Alto: 0.0%
    Medio_Alto: 1.5%
    Medio: 1.6%
    Bajo: 3.5%


In [43]:
# =============================================================================
# CORRELACIONES Y VARIABLES PREDICTIVAS
# =============================================================================

print(f"\nAnálisis correlaciones variables predictivas:")

# Variables clave para análisis de correlación
vars_analisis = [
   'Saldo', 'Limite.Cupo', 'utilizacion_cupo', 'Edad.Mora', 'Vr.Mora',
   'Pago.del.Mes', 'Pago.Minimo', 'ratio_pago', 'cambio_saldo', 'Target'
]

# Filtrar solo variables existentes
vars_disponibles = [v for v in vars_analisis if v in train_clean.columns]

# Matriz de correlación
corr_matrix = train_clean[vars_disponibles].corr()

# Correlaciones con Target (lo más importante para retención)
print(f"  Correlaciones con TARGET (ordenadas por impacto):")
target_corr = corr_matrix['Target'].drop('Target').sort_values(key=abs, ascending=False)

for var, corr in target_corr.items():
   direction = "↑" if corr > 0 else "↓"
   print(f"    {var}: {corr:.3f} {direction}")

# Identificar variables más predictivas
top_predictors = target_corr.abs().head(3)
print(f"\n  Top 3 variables predictivas:")
for i, (var, corr) in enumerate(top_predictors.items(), 1):
   print(f"    {i}. {var} (|r|={corr:.3f})")

# Correlaciones entre variables financieras (multicolinealidad)
print(f"\n  Correlaciones altas entre variables (|r| > 0.7):")
corr_alta = []
for i in range(len(corr_matrix.columns)):
   for j in range(i+1, len(corr_matrix.columns)):
       var1, var2 = corr_matrix.columns[i], corr_matrix.columns[j]
       corr_val = corr_matrix.iloc[i, j]
       if abs(corr_val) > 0.7 and var1 != 'Target' and var2 != 'Target':
           corr_alta.append((var1, var2, corr_val))
           print(f"    {var1} - {var2}: {corr_val:.3f}")

if not corr_alta:
   print(f"    No se detectan correlaciones altas entre predictores")

# Análisis por segmentos de riesgo (sin quintiles)
print(f"\n  Análisis por segmentos de riesgo:")

# Usar variable más predictiva para segmentación simple
var_principal = target_corr.abs().idxmax()
var_values = train_clean[var_principal].dropna()

if len(var_values) > 0:
   # Segmentación en 3 grupos usando percentiles
   p33 = var_values.quantile(0.33)
   p67 = var_values.quantile(0.67)
   
   conditions = [
       train_clean[var_principal] <= p33,
       (train_clean[var_principal] > p33) & (train_clean[var_principal] <= p67),
       train_clean[var_principal] > p67
   ]
   choices = ['Bajo', 'Medio', 'Alto']
   train_clean[f'{var_principal}_segmento'] = np.select(conditions, choices, default='Sin_Dato')
   
   segmento_analysis = train_clean.groupby(f'{var_principal}_segmento')['Target'].agg(['count', 'sum', 'mean']).round(3)
   segmento_analysis.columns = ['Clientes', 'Fugas', 'Tasa_Fuga']
   
   print(f"  Segmentación por {var_principal}:")
   for segmento, row in segmento_analysis.iterrows():
       if segmento != 'Sin_Dato':
           print(f"    {segmento}: {row['Clientes']:,} clientes, {row['Tasa_Fuga']:.1%} fuga")
   
   # Concentración de riesgo
   if 'Alto' in segmento_analysis.index:
       fuga_alto = segmento_analysis.loc['Alto', 'Fugas']
       total_fugas = segmento_analysis['Fugas'].sum()
       concentracion = (fuga_alto / total_fugas * 100) if total_fugas > 0 else 0
       print(f"  Concentración riesgo en segmento Alto: {concentracion:.1f}% de todas las fugas")


Análisis correlaciones variables predictivas:
  Correlaciones con TARGET (ordenadas por impacto):
    utilizacion_cupo: -0.078 ↓
    ratio_pago: 0.066 ↑
    Saldo: -0.056 ↓
    Pago.Minimo: -0.044 ↓
    cambio_saldo: -0.040 ↓
    Edad.Mora: -0.037 ↓
    Vr.Mora: -0.030 ↓
    Pago.del.Mes: 0.025 ↑
    Limite.Cupo: -0.001 ↓

  Top 3 variables predictivas:
    1. utilizacion_cupo (|r|=0.078)
    2. ratio_pago (|r|=0.066)
    3. Saldo (|r|=0.056)

  Correlaciones altas entre variables (|r| > 0.7):
    Vr.Mora - Pago.Minimo: 0.863

  Análisis por segmentos de riesgo:
  Segmentación por utilizacion_cupo:
    Alto: 16,500.0 clientes, 0.9% fuga
    Bajo: 24,047.0 clientes, 1.9% fuga
    Medio: 9,454.0 clientes, 8.5% fuga
  Concentración riesgo en segmento Alto: 11.0% de todas las fugas


In [44]:
# =============================================================================
# VISUALIZACIONES INSIGHTS NEGOCIO
# =============================================================================

print(f"\nGenerando visualizaciones para insights de negocio:")

# Configurar subplot
fig = make_subplots(
   rows=3, cols=2,
   subplot_titles=[
       "Distribución Target vs Benchmark",
       "Riesgo Crediticio vs Fuga",
       "Utilización Cupo por Target", 
       "Mora vs Comportamiento Fuga",
       "Perfil Riesgo vs Tasa Fuga",
       "Correlaciones Variables Clave"
   ],
   specs=[[{"type": "bar"}, {"type": "scatter"}],
          [{"type": "box"}, {"type": "scatter"}],
          [{"type": "bar"}, {"type": "heatmap"}]]
)

# 1. TARGET CON CONTEXTO INDUSTRIA
target_counts = train_clean['Target'].value_counts()
fig.add_trace(
   go.Bar(x=['Colsubsidio', 'Benchmark Industria'], 
          y=[target_counts[1]/(target_counts[0]+target_counts[1])*100, 15],
          text=[f'{target_counts[1]/(target_counts[0]+target_counts[1])*100:.1f}%', '15%'],
          textposition='inside',
          marker_color=['lightcoral', 'lightgray']),
   row=1, col=1
)

# 2. MORA VS UTILIZACIÓN (RIESGO CREDITICIO)
fig.add_trace(
   go.Scatter(x=train_clean[train_clean['Target']==0]['Edad.Mora'],
              y=train_clean[train_clean['Target']==0]['utilizacion_cupo'],
              mode='markers',
              name='No Fuga',
              opacity=0.6,
              marker=dict(color='lightblue', size=4)),
   row=1, col=2
)
fig.add_trace(
   go.Scatter(x=train_clean[train_clean['Target']==1]['Edad.Mora'],
              y=train_clean[train_clean['Target']==1]['utilizacion_cupo'],
              mode='markers',
              name='Fuga',
              opacity=0.8,
              marker=dict(color='red', size=6)),
   row=1, col=2
)

# 3. UTILIZACIÓN CUPO POR TARGET
fig.add_trace(
   go.Box(y=train_clean[train_clean['Target']==0]['utilizacion_cupo'],
          name='No Fuga', marker_color='lightblue'),
   row=2, col=1
)
fig.add_trace(
   go.Box(y=train_clean[train_clean['Target']==1]['utilizacion_cupo'],
          name='Fuga', marker_color='salmon'),
   row=2, col=1
)

# 4. MORA VS CAMBIO SALDO
fig.add_trace(
   go.Scatter(x=train_clean[train_clean['Target']==0]['Edad.Mora'],
              y=train_clean[train_clean['Target']==0]['cambio_saldo'],
              mode='markers',
              name='No Fuga',
              opacity=0.5,
              marker=dict(color='lightblue', size=3)),
   row=2, col=2
)
fig.add_trace(
   go.Scatter(x=train_clean[train_clean['Target']==1]['Edad.Mora'],
              y=train_clean[train_clean['Target']==1]['cambio_saldo'],
              mode='markers',
              name='Fuga',
              opacity=0.8,
              marker=dict(color='red', size=5)),
   row=2, col=2
)

# 5. PERFIL RIESGO VS TASA FUGA
perfil_fuga = train_clean.groupby('perfil_riesgo')['Target'].mean() * 100
fig.add_trace(
   go.Bar(x=perfil_fuga.index,
          y=perfil_fuga.values,
          text=[f'{v:.1f}%' for v in perfil_fuga.values],
          textposition='inside',
          marker_color=['green', 'yellow', 'orange', 'red']),
   row=3, col=1
)

# 6. HEATMAP CORRELACIONES
vars_heatmap = ['utilizacion_cupo', 'Edad.Mora', 'ratio_pago', 'cambio_saldo', 'Target']
corr_subset = train_clean[vars_heatmap].corr()

fig.add_trace(
   go.Heatmap(z=corr_subset.values,
              x=corr_subset.columns,
              y=corr_subset.columns,
              colorscale='RdBu',
              zmid=0,
              text=corr_subset.round(2).values,
              texttemplate="%{text}",
              textfont={"size": 10}),
   row=3, col=2
)

# Layout
fig.update_layout(
   height=1200,
   title_text="EDA COLSUBSIDIO - INSIGHTS MODELO RETENCIÓN",
   showlegend=False
)

fig.update_xaxes(title_text="Días Mora", row=1, col=2)
fig.update_yaxes(title_text="Utilización Cupo", row=1, col=2)
fig.update_xaxes(title_text="Días Mora", row=2, col=2)
fig.update_yaxes(title_text="Cambio Saldo ($)", row=2, col=2)

fig.show()

# Insights clave para modelo
print(f"\nInsights clave para modelo de retención:")
print(f"1. Tasa fuga Colsubsidio ({target_counts[1]/(target_counts[0]+target_counts[1])*100:.1f}%) vs industria (~15%)")
print(f"2. Variable más predictiva: {target_corr.abs().idxmax()} (r={target_corr.abs().max():.3f})")
print(f"3. Perfil alto riesgo: {(train_clean['perfil_riesgo']=='Alto').sum():,} clientes")
print(f"4. Concentración: {train_clean[train_clean['perfil_riesgo']=='Alto']['Target'].mean()*100:.1f}% fuga en alto riesgo")
print(f"5. Desbalance severo: {target_counts[0]/target_counts[1]:.0f}:1 requiere técnicas especiales")


Generando visualizaciones para insights de negocio:



Insights clave para modelo de retención:
1. Tasa fuga Colsubsidio (2.8%) vs industria (~15%)
2. Variable más predictiva: utilizacion_cupo (r=0.078)
3. Perfil alto riesgo: 3,592 clientes
4. Concentración: 0.0% fuga en alto riesgo
5. Desbalance severo: 34:1 requiere técnicas especiales


In [45]:
# =============================================================================
# EDA DEMOGRAFICAS - ANÁLISIS COMPLETO
# =============================================================================

print("=" * 60)
print("EDA DEMOGRAFICAS - PERFIL SOCIODEMOGRÁFICO COLSUBSIDIO")
print("=" * 60)

demograficas = datasets["demograficas"]

# 1. ESTRUCTURA BÁSICA
print(f"Dimensiones: {demograficas.shape[0]:,} registros x {demograficas.shape[1]} columnas")
print(f"Columnas disponibles: {list(demograficas.columns)}")

# 2. CALIDAD GENERAL DE DATOS
print(f"\nCalidad datos por variable:")
for col in demograficas.columns:
   if col != 'id':
       total_registros = len(demograficas)
       valores_nulos = demograficas[col].isnull().sum()
       valores_validos = total_registros - valores_nulos
       pct_completo = (valores_validos / total_registros) * 100
       valores_unicos = demograficas[col].nunique()
       
       print(f"  {col}:")
       print(f"    Completo: {pct_completo:.1f}% ({valores_validos:,}/{total_registros:,})")
       print(f"    Valores únicos: {valores_unicos:,}")

# 3. ANÁLISIS VARIABLE ID (IDENTIFICADOR)
print(f"\nAnálisis identificadores:")
ids_unicos = demograficas['id'].nunique()
ids_duplicados = len(demograficas) - ids_unicos
print(f"  IDs únicos: {ids_unicos:,}")
print(f"  IDs duplicados: {ids_duplicados:,}")
if ids_duplicados > 0:
   print(f"  ⚠ Revisar duplicados en identificadores")

# 4. CATEGORIA AFILIADO (IMPORTANTE)
print(f"\nCategoría de afiliado a Colsubsidio:")
if 'categoria' in demograficas.columns:
   categoria_dist = demograficas['categoria'].value_counts()
   print(f"  Total categorías: {len(categoria_dist)}")
   print(f"  Distribución completa:")
   for cat, count in categoria_dist.items():
       pct = (count / len(demograficas)) * 100
       print(f"    {cat}: {count:,} ({pct:.1f}%)")
   
   # Analizar estructura de categorías
   categoria_unica = demograficas['categoria'].dropna().unique()
   print(f"  Categorías identificadas: {list(categoria_unica)}")
   
   # Verificar si hay patrones en nombres
   if len(categoria_unica) > 1:
       print(f"  Análisis patrones:")
       for cat in sorted(categoria_unica):
           if pd.notna(cat):
               print(f"    '{cat}': {len(str(cat))} caracteres")
else:
   print(f"  ⚠ Variable 'categoria' no encontrada")

# 5. SEGMENTO POBLACIONAL (MODELO ANALÍTICO COLSUBSIDIO)
print(f"\nSegmento poblacional (modelo analítico Colsubsidio):")
if 'segmento' in demograficas.columns:
   segmento_dist = demograficas['segmento'].value_counts()
   print(f"  Total segmentos: {len(segmento_dist)}")
   print(f"  Distribución:")
   for seg, count in segmento_dist.items():
       pct = (count / len(demograficas)) * 100
       print(f"    {seg}: {count:,} ({pct:.1f}%)")
   
   # Verificar patrones en nombres de segmentos
   segmentos_unicos = demograficas['segmento'].dropna().unique()
   print(f"  Segmentos únicos: {list(segmentos_unicos)}")
   
   # Buscar patrones comunes (Básico, Alto, Joven, Medio)
   patrones_segmento = {}
   for seg in segmentos_unicos:
       if pd.notna(seg):
           seg_str = str(seg).lower()
           if 'basico' in seg_str:
               patrones_segmento['Básico'] = patrones_segmento.get('Básico', 0) + demograficas[demograficas['segmento']==seg].shape[0]
           elif 'alto' in seg_str:
               patrones_segmento['Alto'] = patrones_segmento.get('Alto', 0) + demograficas[demograficas['segmento']==seg].shape[0]
           elif 'joven' in seg_str:
               patrones_segmento['Joven'] = patrones_segmento.get('Joven', 0) + demograficas[demograficas['segmento']==seg].shape[0]
           elif 'medio' in seg_str:
               patrones_segmento['Medio'] = patrones_segmento.get('Medio', 0) + demograficas[demograficas['segmento']==seg].shape[0]
   
   if patrones_segmento:
       print(f"  Agrupación por patrones:")
       for patron, count in patrones_segmento.items():
           pct = (count / len(demograficas)) * 100
           print(f"    Segmentos '{patron}': {count:,} ({pct:.1f}%)")
else:
   print(f"  ⚠ Variable 'segmento' no encontrada")

# 6. EDAD
print(f"\nAnálisis edad:")
if 'edad' in demograficas.columns:
   edad_valida = demograficas['edad'].dropna()
   if len(edad_valida) > 0:
       stats_edad = edad_valida.describe()
       print(f"  Estadísticas:")
       print(f"    Rango: {stats_edad['min']:.0f} - {stats_edad['max']:.0f} años")
       print(f"    Promedio: {stats_edad['mean']:.1f} años")
       print(f"    Mediana: {stats_edad['50%']:.0f} años")
       print(f"    Desviación: {stats_edad['std']:.1f} años")
       
       # Validar rangos razonables
       menores_18 = (edad_valida < 18).sum()
       mayores_100 = (edad_valida > 100).sum()
       print(f"  Validación rangos:")
       print(f"    Menores 18 años: {menores_18:,}")
       print(f"    Mayores 100 años: {mayores_100:,}")
       
       if menores_18 > 0 or mayores_100 > 0:
           print(f"    ⚠ Revisar edades fuera de rango esperado")
       
       # Distribución por grupos etarios
       bins_edad = [0, 25, 35, 45, 55, 65, 100]
       labels_edad = ['18-25', '26-35', '36-45', '46-55', '56-65', '65+']
       demograficas['grupo_edad'] = pd.cut(demograficas['edad'], bins=bins_edad, labels=labels_edad, include_lowest=True)
       
       print(f"  Distribución por grupos etarios:")
       grupo_dist = demograficas['grupo_edad'].value_counts().sort_index()
       for grupo, count in grupo_dist.items():
           pct = (count / len(edad_valida)) * 100
           print(f"    {grupo}: {count:,} ({pct:.1f}%)")
else:
   print(f"  ⚠ Variable 'edad' no encontrada")

# 7. NIVEL EDUCATIVO
print(f"\nNivel educativo:")
if 'nivel_educativo' in demograficas.columns:
   edu_dist = demograficas['nivel_educativo'].value_counts()
   print(f"  Total niveles: {len(edu_dist)}")
   print(f"  Distribución:")
   for nivel, count in edu_dist.items():
       pct = (count / len(demograficas)) * 100
       print(f"    {nivel}: {count:,} ({pct:.1f}%)")
   
   # Ordenar por nivel educativo (si es posible)
   niveles_ordenados = ['Sin definir', 'primaria', 'secundaria', 'profesional', 'posgrado']
   print(f"  Jerarquía educativa:")
   for nivel in niveles_ordenados:
       if nivel in edu_dist.index:
           count = edu_dist[nivel]
           pct = (count / len(demograficas)) * 100
           print(f"    {nivel}: {count:,} ({pct:.1f}%)")
else:
   print(f"  ⚠ Variable 'nivel_educativo' no encontrada")

# 8. ESTADO CIVIL
print(f"\nEstado civil:")
if 'estado_civil' in demograficas.columns:
   civil_dist = demograficas['estado_civil'].value_counts()
   print(f"  Total estados: {len(civil_dist)}")
   print(f"  Distribución:")
   for estado, count in civil_dist.items():
       pct = (count / len(demograficas)) * 100
       print(f"    {estado}: {count:,} ({pct:.1f}%)")
else:
   print(f"  ⚠ Variable 'estado_civil' no encontrada")

# 9. GÉNERO
print(f"\nGénero:")
if 'Genero' in demograficas.columns:
   genero_dist = demograficas['Genero'].value_counts()
   print(f"  Total géneros: {len(genero_dist)}")
   print(f"  Distribución:")
   for genero, count in genero_dist.items():
       pct = (count / len(demograficas)) * 100
       print(f"    {genero}: {count:,} ({pct:.1f}%)")
   
   # Analizar balance de género
   if len(genero_dist) >= 2:
       balance = genero_dist.min() / genero_dist.max()
       print(f"  Balance género: {balance:.2f} (1.0 = perfecto balance)")
       if balance < 0.8:
           print(f"    ⚠ Desbalance significativo de género")
else:
   print(f"  ⚠ Variable 'Genero' no encontrada")

EDA DEMOGRAFICAS - PERFIL SOCIODEMOGRÁFICO COLSUBSIDIO
Dimensiones: 55,002 registros x 10 columnas
Columnas disponibles: ['id', 'categoria', 'segmento', 'edad', 'nivel_educativo', 'estado_civil', 'Genero', 'PAC', 'contrato', 'estrato']

Calidad datos por variable:
  categoria:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 3
  segmento:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 4
  edad:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 48
  nivel_educativo:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 4
  estado_civil:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 4
  Genero:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 2
  PAC:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 4
  contrato:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 4
  estrato:
    Completo: 8.0% (4,418/55,002)
    Valores únicos: 5

Análisis identificadores:
  IDs únicos: 55,002
  IDs duplicados: 0

Categoría de afiliado a Colsu

In [46]:
# =============================================================================
# VISUALIZACIONES DEMOGRAFICAS
# =============================================================================

print(f"\nGenerando visualizaciones de las 9 variables demográficas:")

# Configurar subplot para 9 variables
fig = make_subplots(
   rows=3, cols=3,
   subplot_titles=[
       "Categoría Afiliado Colsubsidio",
       "Segmentos Poblacionales",
       "Distribución por Edad",
       "Nivel Educativo",
       "Estado Civil",
       "Distribución por Género",
       "Personas a Cargo (PAC)",
       "Tipos de Contrato",
       "Estratos Socioeconómicos"
   ],
   specs=[[{"type": "bar"}, {"type": "bar"}, {"type": "histogram"}],
          [{"type": "bar"}, {"type": "bar"}, {"type": "bar"}],
          [{"type": "bar"}, {"type": "bar"}, {"type": "bar"}]]
)

# 1. CATEGORÍA AFILIADO
if 'categoria' in demograficas.columns:
   categoria_counts = demograficas['categoria'].value_counts()
   fig.add_trace(
       go.Bar(x=categoria_counts.index,
              y=categoria_counts.values,
              text=[f'{v:,}' for v in categoria_counts.values],
              textposition='inside',
              marker_color='lightblue',
              name='Categoría'),
       row=1, col=1
   )

# 2. SEGMENTOS POBLACIONALES
if 'segmento' in demograficas.columns:
   segmento_counts = demograficas['segmento'].value_counts().head(6)
   fig.add_trace(
       go.Bar(x=segmento_counts.index,
              y=segmento_counts.values,
              text=[f'{v:,}' for v in segmento_counts.values],
              textposition='inside',
              marker_color='lightgreen',
              name='Segmento'),
       row=1, col=2
   )

# 3. DISTRIBUCIÓN EDAD
if 'edad' in demograficas.columns:
   fig.add_trace(
       go.Histogram(x=demograficas['edad'].dropna(),
                    nbinsx=25,
                    marker_color='lightcoral',
                    opacity=0.7,
                    name='Edad'),
       row=1, col=3
   )

# 4. NIVEL EDUCATIVO
if 'nivel_educativo' in demograficas.columns:
   edu_counts = demograficas['nivel_educativo'].value_counts()
   # Ordenar niveles educativos
   orden_educativo = ['Sin definir', 'primaria', 'secundaria', 'profesional', 'posgrado']
   edu_ordenado = {nivel: edu_counts.get(nivel, 0) for nivel in orden_educativo if nivel in edu_counts.index}
   
   if edu_ordenado:
       fig.add_trace(
           go.Bar(x=list(edu_ordenado.keys()),
                  y=list(edu_ordenado.values()),
                  text=[f'{v:,}' for v in edu_ordenado.values()],
                  textposition='inside',
                  marker_color='orange',
                  name='Educación'),
           row=2, col=1
       )
   else:
       fig.add_trace(
           go.Bar(x=edu_counts.index,
                  y=edu_counts.values,
                  text=[f'{v:,}' for v in edu_counts.values],
                  textposition='inside',
                  marker_color='orange',
                  name='Educación'),
           row=2, col=1
       )

# 5. ESTADO CIVIL
if 'estado_civil' in demograficas.columns:
   civil_counts = demograficas['estado_civil'].value_counts()
   fig.add_trace(
       go.Bar(x=civil_counts.index,
              y=civil_counts.values,
              text=[f'{v:,}' for v in civil_counts.values],
              textposition='inside',
              marker_color='purple',
              name='Estado Civil'),
       row=2, col=2
   )

# 6. GÉNERO
if 'Genero' in demograficas.columns:
   genero_counts = demograficas['Genero'].value_counts()
   fig.add_trace(
       go.Bar(x=genero_counts.index,
              y=genero_counts.values,
              text=[f'{v:,}' for v in genero_counts.values],
              textposition='inside',
              marker_color='pink',
              name='Género'),
       row=2, col=3
   )

# 7. PERSONAS A CARGO (PAC)
if 'PAC' in demograficas.columns:
   pac_counts = demograficas['PAC'].value_counts().sort_index().head(8)
   fig.add_trace(
       go.Bar(x=[f'{int(i)}' for i in pac_counts.index],
              y=pac_counts.values,
              text=[f'{v:,}' for v in pac_counts.values],
              textposition='inside',
              marker_color='gold',
              name='PAC'),
       row=3, col=1
   )

# 8. TIPOS CONTRATO
if 'contrato' in demograficas.columns:
   contrato_counts = demograficas['contrato'].value_counts().sort_index()
   contrato_labels = []
   contrato_map = {1: 'Fijo', 2: 'Indefinido', 3: 'Prestación', 4: 'Independiente'}
   
   for codigo in contrato_counts.index:
       contrato_labels.append(contrato_map.get(codigo, f'Tipo {codigo}'))
   
   fig.add_trace(
       go.Bar(x=contrato_labels,
              y=contrato_counts.values,
              text=[f'{v:,}' for v in contrato_counts.values],
              textposition='inside',
              marker_color='cyan',
              name='Contrato'),
       row=3, col=2
   )

# 9. ESTRATOS SOCIOECONÓMICOS (INCLUYENDO FALTANTES)
if 'estrato' in demograficas.columns:
   # Calcular valores faltantes
   total_registros = len(demograficas)
   sin_estrato = demograficas['estrato'].isnull().sum()
   
   # Obtener distribución de estratos válidos
   estrato_counts = demograficas['estrato'].value_counts().sort_index()
   
   # Crear listas para el gráfico incluyendo "Sin Información"
   x_labels = ['Sin Información']
   y_values = [sin_estrato]
   colors = ['lightgray']
   
   # Agregar estratos válidos
   for estrato, count in estrato_counts.items():
       x_labels.append(f'Estrato {int(estrato)}')
       y_values.append(count)
       colors.append('lightsteelblue')
   
   fig.add_trace(
       go.Bar(x=x_labels,
              y=y_values,
              text=[f'{v:,}<br>({v/total_registros*100:.1f}%)' for v in y_values],
              textposition='inside',
              marker_color=colors,
              name='Estrato'),
       row=3, col=3
   )

# Configurar layout
fig.update_layout(
   height=1200,
   title_text="PERFIL DEMOGRÁFICO COMPLETO COLSUBSIDIO - 9 VARIABLES",
   showlegend=False,
   font=dict(size=10)
)

# Rotar etiquetas para mejor legibilidad en gráficos con texto largo
fig.update_xaxes(tickangle=45, row=1, col=1)
fig.update_xaxes(tickangle=45, row=1, col=2)
fig.update_xaxes(tickangle=45, row=2, col=1)
fig.update_xaxes(tickangle=45, row=2, col=2)

# Ajustar tamaño de texto en gráficos
for i in range(1, 4):
   for j in range(1, 4):
       fig.update_xaxes(title_font_size=10, row=i, col=j)
       fig.update_yaxes(title_font_size=10, row=i, col=j)

fig.show()

# Resumen ejecutivo de insights demográficos
print(f"\nInsights demográficos clave:")

# 1. Categoría principal
if 'categoria' in demograficas.columns:
   cat_principal = demograficas['categoria'].value_counts().index[0]
   pct_cat = demograficas['categoria'].value_counts().iloc[0] / len(demograficas) * 100
   print(f"1. Categoría afiliado principal: {cat_principal} ({pct_cat:.1f}%)")

# 2. Segmento dominante
if 'segmento' in demograficas.columns:
   seg_principal = demograficas['segmento'].value_counts().index[0]
   pct_seg = demograficas['segmento'].value_counts().iloc[0] / len(demograficas) * 100
   print(f"2. Segmento poblacional principal: {seg_principal} ({pct_seg:.1f}%)")

# 3. Perfil etario
if 'edad' in demograficas.columns:
   edad_promedio = demograficas['edad'].mean()
   edad_mediana = demograficas['edad'].median()
   print(f"3. Perfil etario: promedio {edad_promedio:.1f} años, mediana {edad_mediana:.0f} años")

# 4. Nivel educativo predominante
if 'nivel_educativo' in demograficas.columns:
   edu_principal = demograficas['nivel_educativo'].value_counts().index[0]
   pct_edu = demograficas['nivel_educativo'].value_counts().iloc[0] / len(demograficas) * 100
   print(f"4. Nivel educativo principal: {edu_principal} ({pct_edu:.1f}%)")

# 5. Estrato socioeconómico (incluyendo análisis de faltantes)
if 'estrato' in demograficas.columns:
   sin_estrato_pct = sin_estrato / total_registros * 100
   print(f"5. Estrato: {sin_estrato_pct:.1f}% sin información")
   if len(estrato_counts) > 0:
       estrato_principal = estrato_counts.index[0]
       pct_estrato_principal = estrato_counts.iloc[0] / total_registros * 100
       print(f"   Estrato más común: {estrato_principal:.0f} ({pct_estrato_principal:.1f}% del total)")

# 6. Distribución género
if 'Genero' in demograficas.columns:
   genero_dist = demograficas['Genero'].value_counts()
   genero_principal = genero_dist.index[0]
   pct_genero = genero_dist.iloc[0] / len(demograficas) * 100
   print(f"6. Género predominante: {genero_principal} ({pct_genero:.1f}%)")

# 7. Tipo contrato más común
if 'contrato' in demograficas.columns:
   contrato_principal = demograficas['contrato'].value_counts().index[0]
   contrato_map = {1: 'Fijo', 2: 'Indefinido', 3: 'Prestación', 4: 'Independiente'}
   nombre_contrato = contrato_map.get(contrato_principal, f'Tipo {contrato_principal}')
   pct_contrato = demograficas['contrato'].value_counts().iloc[0] / len(demograficas) * 100
   print(f"7. Tipo contrato principal: {nombre_contrato} ({pct_contrato:.1f}%)")

# 8. Calidad general
completitud_promedio = (1 - demograficas.isnull().mean().mean()) * 100
print(f"8. Completitud promedio datos: {completitud_promedio:.1f}%")
print(f"9. Total registros únicos: {demograficas['id'].nunique():,}")

print(f"\nEDA DEMOGRAFICAS COMPLETADO - Dataset analizado independientemente")


Generando visualizaciones de las 9 variables demográficas:



Insights demográficos clave:
1. Categoría afiliado principal: A (55.0%)
2. Segmento poblacional principal: Segemnto_Basico (46.8%)
3. Perfil etario: promedio 41.5 años, mediana 41 años
4. Nivel educativo principal: primaria (52.7%)
5. Estrato: 92.0% sin información
   Estrato más común: 1 (3.5% del total)
6. Género predominante: M (50.2%)
7. Tipo contrato principal: Indefinido (25.6%)
8. Completitud promedio datos: 91.6%
9. Total registros únicos: 55,002

EDA DEMOGRAFICAS COMPLETADO - Dataset analizado independientemente


In [47]:
# =============================================================================
# EDA SUBSIDIOS - ANÁLISIS COMPLETO BENEFICIOS COLSUBSIDIO
# =============================================================================

print("=" * 60)
print("EDA SUBSIDIOS - BENEFICIOS ECOSISTEMA COLSUBSIDIO")
print("=" * 60)

subsidios = datasets["subsidios"]

# 1. ESTRUCTURA BÁSICA
print(f"Dimensiones: {subsidios.shape[0]:,} registros x {subsidios.shape[1]} columnas")
print(f"Columnas disponibles: {list(subsidios.columns)}")

# 2. CALIDAD GENERAL DE DATOS
print(f"\nCalidad datos por beneficio:")
for col in subsidios.columns:
   if col != 'id':
       total_registros = len(subsidios)
       valores_nulos = subsidios[col].isnull().sum()
       valores_validos = total_registros - valores_nulos
       pct_completo = (valores_validos / total_registros) * 100
       valores_unicos = subsidios[col].nunique()
       
       print(f"  {col}:")
       print(f"    Completo: {pct_completo:.1f}% ({valores_validos:,}/{total_registros:,})")
       print(f"    Valores únicos: {valores_unicos:,}")

# 3. ANÁLISIS CUOTA MONETARIA
print(f"\nCuota Monetaria (derecho a subsidio monetario):")
if 'cuota_monetaria' in subsidios.columns:
   cuota_dist = subsidios['cuota_monetaria'].value_counts().sort_index()
   total = len(subsidios)
   
   print(f"  Distribución:")
   for codigo, count in cuota_dist.items():
       pct = (count / total) * 100
       if codigo == 1:
           print(f"    Código 1 (Con derecho): {count:,} ({pct:.1f}%)")
       elif codigo == 2:
           print(f"    Código 2 (Sin derecho): {count:,} ({pct:.1f}%)")
       else:
           print(f"    Código {codigo}: {count:,} ({pct:.1f}%)")
   
   # Calcular penetración del beneficio
   con_derecho = cuota_dist.get(1, 0)
   penetracion_cuota = (con_derecho / total) * 100
   print(f"  Penetración cuota monetaria: {penetracion_cuota:.1f}%")
   
   # Verificar códigos válidos
   codigos_validos = {1, 2}
   codigos_encontrados = set(subsidios['cuota_monetaria'].dropna().unique())
   codigos_invalidos = codigos_encontrados - codigos_validos
   if codigos_invalidos:
       print(f"  ⚠ Códigos no válidos encontrados: {codigos_invalidos}")
else:
   print(f"  ⚠ Variable 'cuota_monetaria' no encontrada")

# 4. ANÁLISIS SUBSIDIO VIVIENDA
print(f"\nSubsidio Vivienda (solicitud y desembolso):")
if 'sub_vivenda' in subsidios.columns:
   vivienda_dist = subsidios['sub_vivenda'].value_counts().sort_index()
   
   print(f"  Distribución:")
   for codigo, count in vivienda_dist.items():
       pct = (count / total) * 100
       if codigo == 1:
           print(f"    Código 1 (Ha solicitado/desembolsado): {count:,} ({pct:.1f}%)")
       elif codigo == 2:
           print(f"    Código 2 (No ha solicitado): {count:,} ({pct:.1f}%)")
       else:
           print(f"    Código {codigo}: {count:,} ({pct:.1f}%)")
   
   # Penetración subsidio vivienda
   ha_solicitado = vivienda_dist.get(1, 0)
   penetracion_vivienda = (ha_solicitado / total) * 100
   print(f"  Penetración subsidio vivienda: {penetracion_vivienda:.1f}%")
   
   # Verificar códigos válidos
   codigos_validos = {1, 2}
   codigos_encontrados = set(subsidios['sub_vivenda'].dropna().unique())
   codigos_invalidos = codigos_encontrados - codigos_validos
   if codigos_invalidos:
       print(f"  ⚠ Códigos no válidos encontrados: {codigos_invalidos}")
else:
   print(f"  ⚠ Variable 'sub_vivenda' no encontrada")

# 5. ANÁLISIS BONO LONCHERA
print(f"\nBono Lonchera (beneficio familiar):")
if 'bono_lonchera' in subsidios.columns:
   lonchera_dist = subsidios['bono_lonchera'].value_counts().sort_index()
   
   print(f"  Distribución:")
   for codigo, count in lonchera_dist.items():
       pct = (count / total) * 100
       if codigo == 1:
           print(f"    Código 1 (Con derecho): {count:,} ({pct:.1f}%)")
       elif codigo == 2:
           print(f"    Código 2 (Sin derecho): {count:,} ({pct:.1f}%)")
       else:
           print(f"    Código {codigo}: {count:,} ({pct:.1f}%)")
   
   # Penetración bono lonchera
   con_derecho_lonchera = lonchera_dist.get(1, 0)
   penetracion_lonchera = (con_derecho_lonchera / total) * 100
   print(f"  Penetración bono lonchera: {penetracion_lonchera:.1f}%")
   
   # Verificar códigos válidos
   codigos_validos = {1, 2}
   codigos_encontrados = set(subsidios['bono_lonchera'].dropna().unique())
   codigos_invalidos = codigos_encontrados - codigos_validos
   if codigos_invalidos:
       print(f"  ⚠ Códigos no válidos encontrados: {codigos_invalidos}")
else:
   print(f"  ⚠ Variable 'bono_lonchera' no encontrada")

# 6. ANÁLISIS CRUZADO DE BENEFICIOS
print(f"\nAnálisis combinado beneficios (Engagement Ecosistema):")

# Crear variables binarias para análisis
subsidios_analysis = subsidios.copy()
if 'cuota_monetaria' in subsidios.columns:
   subsidios_analysis['tiene_cuota'] = (subsidios_analysis['cuota_monetaria'] == 1).astype(int)
if 'sub_vivenda' in subsidios.columns:
   subsidios_analysis['uso_vivienda'] = (subsidios_analysis['sub_vivenda'] == 1).astype(int)
if 'bono_lonchera' in subsidios.columns:
   subsidios_analysis['tiene_lonchera'] = (subsidios_analysis['bono_lonchera'] == 1).astype(int)

# Calcular engagement total
beneficios_cols = ['tiene_cuota', 'uso_vivienda', 'tiene_lonchera']
beneficios_disponibles = [col for col in beneficios_cols if col in subsidios_analysis.columns]

if beneficios_disponibles:
   subsidios_analysis['total_beneficios'] = subsidios_analysis[beneficios_disponibles].sum(axis=1)
   
   print(f"  Distribución engagement (número de beneficios activos):")
   engagement_dist = subsidios_analysis['total_beneficios'].value_counts().sort_index()
   for num_beneficios, count in engagement_dist.items():
       pct = (count / total) * 100
       print(f"    {num_beneficios} beneficios: {count:,} ({pct:.1f}%)")
   
   # Segmentación por engagement
   sin_beneficios = engagement_dist.get(0, 0)
   un_beneficio = engagement_dist.get(1, 0)
   dos_beneficios = engagement_dist.get(2, 0)
   tres_beneficios = engagement_dist.get(3, 0)
   
   print(f"\n  Segmentación engagement:")
   print(f"    Sin beneficios: {sin_beneficios:,} ({sin_beneficios/total*100:.1f}%)")
   print(f"    Engagement bajo (1): {un_beneficio:,} ({un_beneficio/total*100:.1f}%)")
   print(f"    Engagement medio (2): {dos_beneficios:,} ({dos_beneficios/total*100:.1f}%)")
   print(f"    Engagement alto (3): {tres_beneficios:,} ({tres_beneficios/total*100:.1f}%)")
   
   # Índice de engagement promedio
   engagement_promedio = subsidios_analysis['total_beneficios'].mean()
   print(f"    Engagement promedio: {engagement_promedio:.2f} beneficios por cliente")

# 7. COMBINACIONES MÁS COMUNES
print(f"\nCombinaciones de beneficios más frecuentes:")
if len(beneficios_disponibles) >= 2:
   # Crear combinaciones
   subsidios_analysis['perfil_beneficios'] = ''
   
   for _, row in subsidios_analysis.iterrows():
       perfil = []
       if 'tiene_cuota' in subsidios_analysis.columns and row['tiene_cuota'] == 1:
           perfil.append('Cuota')
       if 'uso_vivienda' in subsidios_analysis.columns and row['uso_vivienda'] == 1:
           perfil.append('Vivienda')
       if 'tiene_lonchera' in subsidios_analysis.columns and row['tiene_lonchera'] == 1:
           perfil.append('Lonchera')
       
       if not perfil:
           subsidios_analysis.loc[subsidios_analysis.index[len(perfil_counts) if 'perfil_counts' in locals() else _], 'perfil_beneficios'] = 'Sin_Beneficios'
       else:
           subsidios_analysis.loc[subsidios_analysis.index[len(perfil_counts) if 'perfil_counts' in locals() else _], 'perfil_beneficios'] = '+'.join(perfil)
   
   # Rehacer con método más eficiente
   perfiles = []
   for _, row in subsidios_analysis.iterrows():
       perfil = []
       if 'tiene_cuota' in subsidios_analysis.columns and row['tiene_cuota'] == 1:
           perfil.append('Cuota')
       if 'uso_vivienda' in subsidios_analysis.columns and row['uso_vivienda'] == 1:
           perfil.append('Vivienda')
       if 'tiene_lonchera' in subsidios_analysis.columns and row['tiene_lonchera'] == 1:
           perfil.append('Lonchera')
       
       if not perfil:
           perfiles.append('Sin_Beneficios')
       else:
           perfiles.append('+'.join(perfil))
   
   subsidios_analysis['perfil_beneficios'] = perfiles
   perfil_counts = subsidios_analysis['perfil_beneficios'].value_counts()
   
   print(f"  Top 5 combinaciones:")
   for perfil, count in perfil_counts.head().items():
       pct = (count / total) * 100
       print(f"    {perfil}: {count:,} ({pct:.1f}%)")

# 8. RESUMEN PENETRACIÓN BENEFICIOS
print(f"\nResumen penetración beneficios Colsubsidio:")
penetraciones = {}
if 'cuota_monetaria' in subsidios.columns:
   penetraciones['Cuota Monetaria'] = (subsidios['cuota_monetaria'] == 1).sum() / len(subsidios) * 100
if 'sub_vivenda' in subsidios.columns:
   penetraciones['Subsidio Vivienda'] = (subsidios['sub_vivenda'] == 1).sum() / len(subsidios) * 100
if 'bono_lonchera' in subsidios.columns:
   penetraciones['Bono Lonchera'] = (subsidios['bono_lonchera'] == 1).sum() / len(subsidios) * 100

for beneficio, penetracion in penetraciones.items():
   print(f"  {beneficio}: {penetracion:.1f}%")

if penetraciones:
   penetracion_promedio = sum(penetraciones.values()) / len(penetraciones)
   print(f"  Penetración promedio: {penetracion_promedio:.1f}%")

# 9. INSIGHTS ESTRATÉGICOS
print(f"\nInsights estratégicos beneficios:")
if len(beneficios_disponibles) > 0:
   clientes_sin_beneficios = (subsidios_analysis['total_beneficios'] == 0).sum()
   pct_sin_beneficios = (clientes_sin_beneficios / total) * 100
   print(f"1. {pct_sin_beneficios:.1f}% clientes sin ningún beneficio activo")
   
   if engagement_promedio < 1.5:
       print(f"2. Engagement bajo: promedio {engagement_promedio:.2f} beneficios/cliente")
       print(f"3. Oportunidad de activación de beneficios subutilizados")
   
   # Beneficio más penetrado
   if penetraciones:
       beneficio_top = max(penetraciones, key=penetraciones.get)
       print(f"4. Beneficio más utilizado: {beneficio_top} ({penetraciones[beneficio_top]:.1f}%)")

print(f"\nEDA SUBSIDIOS COMPLETADO - Análisis de engagement ecosistema Colsubsidio")

# Actualizar datasets
datasets["subsidios_procesado"] = subsidios_analysis

EDA SUBSIDIOS - BENEFICIOS ECOSISTEMA COLSUBSIDIO
Dimensiones: 55,002 registros x 4 columnas
Columnas disponibles: ['id', 'cuota_monetaria', 'sub_vivenda', 'bono_lonchera']

Calidad datos por beneficio:
  cuota_monetaria:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 2
  sub_vivenda:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 2
  bono_lonchera:
    Completo: 100.0% (55,002/55,002)
    Valores únicos: 2

Cuota Monetaria (derecho a subsidio monetario):
  Distribución:
    Código 0: 13,722 (24.9%)
    Código 1 (Con derecho): 41,280 (75.1%)
  Penetración cuota monetaria: 75.1%
  ⚠ Códigos no válidos encontrados: {0}

Subsidio Vivienda (solicitud y desembolso):
  Distribución:
    Código 0: 54,921 (99.9%)
    Código 1 (Ha solicitado/desembolsado): 81 (0.1%)
  Penetración subsidio vivienda: 0.1%
  ⚠ Códigos no válidos encontrados: {0}

Bono Lonchera (beneficio familiar):
  Distribución:
    Código 0: 20,271 (36.9%)
    Código 1 (Con derecho): 34,731 (63.1%)
  Penetra

In [48]:
# =============================================================================
# VISUALIZACIONES SUBSIDIOS - BENEFICIOS ECOSISTEMA COLSUBSIDIO (CORREGIDO)
# =============================================================================

print(f"\nGenerando visualizaciones beneficios Colsubsidio:")

# Configurar subplot para análisis de subsidios
fig = make_subplots(
   rows=2, cols=3,
   subplot_titles=[
       "Penetración Cuota Monetaria",
       "Uso Subsidio Vivienda", 
       "Acceso Bono Lonchera",
       "Engagement Total (Número Beneficios)",
       "Combinaciones Beneficios Más Comunes",
       "Comparativo Penetración Beneficios"
   ],
   specs=[[{"type": "bar"}, {"type": "bar"}, {"type": "bar"}],
          [{"type": "bar"}, {"type": "bar"}, {"type": "bar"}]]
)

# Definir colores para beneficios
color_si = 'lightgreen'
color_no = 'lightcoral'

# 1. CUOTA MONETARIA
if 'cuota_monetaria' in subsidios.columns:
   cuota_counts = subsidios['cuota_monetaria'].value_counts().sort_index()
   labels_cuota = ['Con Derecho', 'Sin Derecho']
   colors_cuota = [color_si, color_no]
   
   fig.add_trace(
       go.Bar(x=labels_cuota,
              y=cuota_counts.values,
              text=[f'{v:,}<br>({v/len(subsidios)*100:.1f}%)' for v in cuota_counts.values],
              textposition='inside',
              marker_color=colors_cuota),
       row=1, col=1
   )

# 2. SUBSIDIO VIVIENDA
if 'sub_vivenda' in subsidios.columns:
   vivienda_counts = subsidios['sub_vivenda'].value_counts().sort_index()
   labels_vivienda = ['Ha Solicitado', 'No Ha Solicitado']
   colors_vivienda = [color_si, color_no]
   
   fig.add_trace(
       go.Bar(x=labels_vivienda,
              y=vivienda_counts.values,
              text=[f'{v:,}<br>({v/len(subsidios)*100:.1f}%)' for v in vivienda_counts.values],
              textposition='inside',
              marker_color=colors_vivienda),
       row=1, col=2
   )

# 3. BONO LONCHERA
if 'bono_lonchera' in subsidios.columns:
   lonchera_counts = subsidios['bono_lonchera'].value_counts().sort_index()
   labels_lonchera = ['Con Derecho', 'Sin Derecho']
   colors_lonchera = [color_si, color_no]
   
   fig.add_trace(
       go.Bar(x=labels_lonchera,
              y=lonchera_counts.values,
              text=[f'{v:,}<br>({v/len(subsidios)*100:.1f}%)' for v in lonchera_counts.values],
              textposition='inside',
              marker_color=colors_lonchera),
       row=1, col=3
   )

# 4. ENGAGEMENT TOTAL
if 'total_beneficios' in subsidios_analysis.columns:
   engagement_counts = subsidios_analysis['total_beneficios'].value_counts().sort_index()
   colors_engagement = ['red', 'orange', 'yellow', 'green']
   
   fig.add_trace(
       go.Bar(x=[f'{int(i)} beneficios' for i in engagement_counts.index],
              y=engagement_counts.values,
              text=[f'{v:,}<br>({v/len(subsidios)*100:.1f}%)' for v in engagement_counts.values],
              textposition='inside',
              marker_color=colors_engagement[:len(engagement_counts)]),
       row=2, col=1
   )

# 5. COMBINACIONES MÁS COMUNES
if 'perfil_beneficios' in subsidios_analysis.columns:
   perfil_counts = subsidios_analysis['perfil_beneficios'].value_counts().head(6)
   
   fig.add_trace(
       go.Bar(x=perfil_counts.index,
              y=perfil_counts.values,
              text=[f'{v:,}' for v in perfil_counts.values],
              textposition='inside',
              marker_color='lightblue'),
       row=2, col=2
   )

# 6. COMPARATIVO PENETRACIÓN (CORREGIDO)
penetraciones_data = {}
if 'cuota_monetaria' in subsidios.columns:
   penetraciones_data['Cuota Monetaria'] = (subsidios['cuota_monetaria'] == 1).sum() / len(subsidios) * 100
if 'sub_vivenda' in subsidios.columns:
   penetraciones_data['Subsidio Vivienda'] = (subsidios['sub_vivenda'] == 1).sum() / len(subsidios) * 100
if 'bono_lonchera' in subsidios.columns:
   penetraciones_data['Bono Lonchera'] = (subsidios['bono_lonchera'] == 1).sum() / len(subsidios) * 100

if penetraciones_data:
   # Definir colores específicos válidos
   colores_penetracion = ['gold', 'lightblue', 'lightcoral']
   
   fig.add_trace(
       go.Bar(x=list(penetraciones_data.keys()),
              y=list(penetraciones_data.values()),
              text=[f'{v:.1f}%' for v in penetraciones_data.values()],
              textposition='inside',
              marker_color=colores_penetracion[:len(penetraciones_data)]),
       row=2, col=3
   )

# Configurar layout
fig.update_layout(
   height=900,
   title_text="BENEFICIOS ECOSISTEMA COLSUBSIDIO - ANÁLISIS ENGAGEMENT",
   showlegend=False,
   font=dict(size=11)
)

# Rotar etiquetas en gráfico de combinaciones
fig.update_xaxes(tickangle=45, row=2, col=2)

# Configurar ejes Y como porcentaje en el comparativo
fig.update_yaxes(title_text="Penetración (%)", row=2, col=3)

fig.show()

# Insights visuales clave
print(f"\nInsights visuales beneficios:")

# 1. Penetración individual
if penetraciones_data:
   beneficio_mayor = max(penetraciones_data, key=penetraciones_data.get)
   beneficio_menor = min(penetraciones_data, key=penetraciones_data.get)
   print(f"1. Mayor penetración: {beneficio_mayor} ({penetraciones_data[beneficio_mayor]:.1f}%)")
   print(f"2. Menor penetración: {beneficio_menor} ({penetraciones_data[beneficio_menor]:.1f}%)")

# 2. Engagement
if 'total_beneficios' in subsidios_analysis.columns:
   sin_beneficios = (subsidios_analysis['total_beneficios'] == 0).sum()
   pct_sin_beneficios = sin_beneficios / len(subsidios) * 100
   con_todos = (subsidios_analysis['total_beneficios'] == 3).sum()
   pct_con_todos = con_todos / len(subsidios) * 100
   
   print(f"3. Sin beneficios: {pct_sin_beneficios:.1f}% ({sin_beneficios:,} clientes)")
   print(f"4. Con todos los beneficios: {pct_con_todos:.1f}% ({con_todos:,} clientes)")

# 3. Combinación más común
if 'perfil_beneficios' in subsidios_analysis.columns:
   combinacion_top = subsidios_analysis['perfil_beneficios'].value_counts().index[0]
   count_top = subsidios_analysis['perfil_beneficios'].value_counts().iloc[0]
   pct_top = count_top / len(subsidios) * 100
   print(f"5. Combinación más común: {combinacion_top} ({pct_top:.1f}%)")

# 4. Oportunidades
if penetraciones_data:
   penetracion_promedio = sum(penetraciones_data.values()) / len(penetraciones_data)
   print(f"6. Penetración promedio: {penetracion_promedio:.1f}%")
   
   if penetracion_promedio < 50:
       print(f"7. Oportunidad: Baja penetración general de beneficios")
   
   gap_penetracion = max(penetraciones_data.values()) - min(penetraciones_data.values())
   if gap_penetracion > 20:
       print(f"8. Gap significativo entre beneficios: {gap_penetracion:.1f} puntos porcentuales")

print(f"\nEDA SUBSIDIOS VISUALIZADO - Análisis engagement ecosistema completado")


Generando visualizaciones beneficios Colsubsidio:



Insights visuales beneficios:
1. Mayor penetración: Cuota Monetaria (75.1%)
2. Menor penetración: Subsidio Vivienda (0.1%)
3. Sin beneficios: 24.9% (13,702 clientes)
4. Con todos los beneficios: 0.1% (54 clientes)
5. Combinación más común: Cuota+Lonchera (63.0%)
6. Penetración promedio: 46.1%
7. Oportunidad: Baja penetración general de beneficios
8. Gap significativo entre beneficios: 74.9 puntos porcentuales

EDA SUBSIDIOS VISUALIZADO - Análisis engagement ecosistema completado
